# Geodesic Regression on Parameterized Hippocampus data!

## Step 1: get brain data to have same parameterization

we will get each brain mesh to have the same parameterization by: 
- choosing the first day to be the "template mesh".
- drawing a geodesic between the "template mesh" and all the other meshes using H2_SurfaceMatch
- H2_SurfaceMatch will make the parameterization of the target match the parameterization of the source.

In [1]:
import glob
import itertools
import multiprocessing
import os
import subprocess
import sys
import time
import warnings

import torch
import trimesh

os.environ["GEOMSTATS_BACKEND"] = "pytorch"
import geomstats.backend as gs
import my28brains.default_config as default_config
import my28brains.discrete_surfaces

from geomstats.geometry.discrete_surfaces import (
    DiscreteSurfaces,
    ElasticMetric,
)

INFO: Using pytorch backend


This will be done in main.py. You can "activate" the reparameterization code by going into default_config and making 

In [2]:
import setcwd
setcwd.main()

import H2_SurfaceMatch.H2_match  # noqa: E402
import H2_SurfaceMatch.utils.input_output  # noqa: E402
import H2_SurfaceMatch.utils.utils  # noqa: E402

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


## 1.1 Load Data

In [3]:
hemisphere = "left"
structure_id = -1

string_base = os.path.join(
    parameterized_meshes_dir,
    f"{hemisphere}_structure_{structure_id}**.ply",
)
paths = sorted(glob.glob(string_base))
print(string_base)
print(paths)

/home/adele/code/my28brains/my28brains/results/meshes_parameterized/left_structure_-1**.ply
['/home/adele/code/my28brains/my28brains/results/meshes_parameterized/left_structure_-1_day02_at_0.0_parameterized.ply', '/home/adele/code/my28brains/my28brains/results/meshes_parameterized/left_structure_-1_day03_at_0.0_parameterized.ply', '/home/adele/code/my28brains/my28brains/results/meshes_parameterized/left_structure_-1_day04_at_0.0_parameterized.ply', '/home/adele/code/my28brains/my28brains/results/meshes_parameterized/left_structure_-1_day05_at_0.0_parameterized.ply', '/home/adele/code/my28brains/my28brains/results/meshes_parameterized/left_structure_-1_day06_at_0.0_parameterized.ply', '/home/adele/code/my28brains/my28brains/results/meshes_parameterized/left_structure_-1_day07_at_0.0_parameterized.ply', '/home/adele/code/my28brains/my28brains/results/meshes_parameterized/left_structure_-1_day08_at_0.0_parameterized.ply', '/home/adele/code/my28brains/my28brains/results/meshes_parameterize

In [4]:
all_vertices = []
all_faces = []
for path in paths:
    [
        one_vertices,
        one_faces,
        FunS,
    ] = H2_SurfaceMatch.utils.input_output.loadData(path)
    all_vertices.append(one_vertices)
    all_faces.append(one_faces)
all_faces = gs.array(all_faces)
all_vertices = gs.array(all_vertices)

# prove they are parameterized the same way
for one_vertices in all_vertices:
    print(one_vertices.shape)
    # print(one_vertices)

torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])
torch.Size([1185, 3])


# Step 2: Take the re-parameterized mesh sequence, and perform geodesic regression on it.

In [5]:
from geomstats.learning.geodesic_regression import GeodesicRegression

In [6]:
# Define Surface Space
# print(all_faces[0])
SURFACE_SPACE = DiscreteSurfaces(faces=all_faces[0])

# METRIC = ElasticMetric(
#     space = SURFACE_SPACE,
#     a0=default_config.a0,
#     a1=default_config.a1,
#     b1=default_config.b1,
#     c1=default_config.c1,
#     d1=default_config.d1,
#     a2=default_config.a2,)

METRIC = ElasticMetric(
    space=SURFACE_SPACE,
    a0=default_config.a0,
    a1=0,
    b1=0,
    c1=0,
    d1=0,
    a2=default_config.a2,
)

In [7]:
print(all_vertices.shape)

torch.Size([29, 1185, 3])


In [ ]:
n_times = len(all_vertices)

times = gs.arange(0, 1, 1 / n_times)
print(times)


# maxiter was 100
gr = GeodesicRegression(
    SURFACE_SPACE,
    metric=METRIC,
    center_X=False,
    method="riemannian",
    max_iter=5,
    init_step_size=0.1,
    verbose=True,
    initialization="frechet",
)

gr.fit(times, all_vertices, compute_training_score=False)

intercept_hat, coef_hat = gr.intercept_, gr.coef_

tensor([0.0000, 0.0345, 0.0690, 0.1034, 0.1379, 0.1724, 0.2069, 0.2414, 0.2759,
        0.3103, 0.3448, 0.3793, 0.4138, 0.4483, 0.4828, 0.5172, 0.5517, 0.5862,
        0.6207, 0.6552, 0.6897, 0.7241, 0.7586, 0.7931, 0.8276, 0.8621, 0.8966,
        0.9310, 0.9655])
LOG before squeeze:
point.shape:  torch.Size([29, 1185, 3])
base_point.shape:  torch.Size([1185, 3])
one_point.shape:  torch.Size([1185, 3])
one_base_point.shape:  torch.Size([1185, 3])
before dimension expansion:
midpoints.shape torch.Size([3, 1185, 3])
initial_point.shape torch.Size([1185, 3])
end_point.shape torch.Size([1185, 3])
after dimension expansion:
midpoints.shape torch.Size([1, 3, 1185, 3])
initial_point.shape torch.Size([1, 1185, 3])
end_point.shape torch.Size([1, 1185, 3])
num_points 1
one_midpoint torch.Size([3, 1185, 3])
one_initial_point torch.Size([1185, 3])
one_endpoint torch.Size([1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])

 This problem is unconstrained.
 This problem is unconstrained.


one_midpoint torch.Size([3, 1185, 3])
one_initial_point torch.Size([1185, 3])
one_endpoint torch.Size([1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
one_midpoint torch.Size([3, 1185, 3])
one_initial_point torch.Size([1185, 3])
one_endpoint torch.Size([1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
one_midpoint torch.Size([3, 1185, 3])
one_initial_point torch.Size([1185, 3])
one_endpoint torch.Size([1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base


 Bad direction in the line search;
   refresh the lbfgs memory and restart the iteration.


INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])

At iterate  530    f=          NaN    |proj g|=  2.41093D+10
one_midpoint torch.Size([3, 1185, 3])
one_initial_point torch.Size([1185, 3])
one_endpoint torch.Size([1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
one_midpoint torch.Size([3, 1185, 3])
one_initial_point torch.Size([1185, 3])
one_endpoint torch.Size([1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h tor

...


           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
10665    111    733      2     8     0   6.631D+08         NaN
  F =                       NaN

ABNORMAL_TERMINATION_IN_LNSRCH                              
one_point.shape:  torch.Size([1185, 3])
one_base_point.shape:  torch.Size([1185, 3])
before dimension expansion:
midpoints.shape torch.Size([3, 1185, 3])
initial_point.shape torch.Size([1185, 3])
end_point.shape torch.Size([1185, 3])
after dimension expansion:
midpoints.shape torch.Size([1, 3, 1185, 3])
initial_point.shape torch.Size([1, 1185, 3])
end_point.shape torch.Size([1, 1185, 3])
num_points 1
one_midpoint torch.


 Bad direction in the line search;
   refresh the lbfgs memory and restart the iteration.


one_midpoint torch.Size([3, 1185, 3])
one_initial_point torch.Size([1185, 3])
one_endpoint torch.Size([1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
one_midpoint torch.Size([3, 1185, 3])
one_initial_point torch.Size([1185, 3])
one_endpoint torch.Size([1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
one_midpoint torch.Size([3, 1185, 3])
one_initial_point torch.Size([1185, 3])
one_endpoint torch.Size([1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base


 Bad direction in the line search;
   refresh the lbfgs memory and restart the iteration.


INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
one_midpoint torch.Size([3, 1185, 3])
one_initial_point torch.Size([1185, 3])
one_endpoint torch.Size([1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
one_midpoint torch.Size([3, 1185, 3])
one_initial_point torch.Size([1185, 3])
one_endpoint torch.Size([1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNER PRODUCT
h torch.Size([1, 1185, 3])
base_point torch.Size([1, 1185, 3])
INNE

In [ ]:
true_intercept_mesh = trimesh.Trimesh(vertices=all_vertices[28], faces=all_faces[0])

intercept_hat_mesh = trimesh.Trimesh(vertices=intercept_hat, faces=all_faces[0])

In [ ]:
true_intercept_mesh.show()

In [ ]:
intercept_hat_mesh.show()